In [1]:
import tqdm
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as anm
import matplotlib.gridspec as gridspec
import matplotlib.animation as anim

In [2]:
class house:
    def __init__(self, dimensions, step, border_indexes, radiators_indexes, doors_indexes, windows_indexes):
        self.windows = windows_indexes
        self.doors = doors_indexes
        self.radiators = list(radiators_indexes.values())
        self.dimensions = dimensions
        self.step = step
        self.border_indexes = border_indexes
        self.matrix = np.zeros((3601, 30, 30))
        self.rooms = []
        for number, room in self.border_indexes.items():
            self.matrix[:, min(list(zip(*room))[0]):max(list(zip(*room))[0]), min(list(zip(*room))[1]):max(list(zip(*room))[1])] = 288 
            self.rooms.append(self.matrix[:, min(list(zip(*room))[0]):max(list(zip(*room))[0]), min(list(zip(*room))[1]):max(list(zip(*room))[1])].view())

    def welcome(self):
        plt.imshow(self.matrix[0,:,:])
    def show_rooms(self):
        return self.rooms
    def show_map(self):
        tmp = self.matrix.copy()
        tmp[self.matrix != 0] = 1
        plt.imshow(tmp)
    def calculate(self):
        f = 0.5
        h_x, h_t = 1, 1
        
        x = np.arange(0, np.shape(self.rooms[0])[2], h_x)
        y = np.arange(0, np.shape(self.rooms[0])[1], h_x)
        x, y = np.meshgrid(x, y, copy=False)
        t = np.arange(0, 60*60+h_t, h_t)

        diff_coeff = 0.01
        ################################

        for j in np.arange(1,len(t),1): 
            for k in range(len(self.border_indexes)): #pętla po pokojach
                self.rooms[k][j, 1:-1 , 1:-1] = self.rooms[k][j-1, 1:-1 , 1:-1] + diff_coeff*h_t/h_x**2*(self.rooms[k][j-1, 2:, 1:-1] + self.rooms[k][j-1, 0:-2, 1:-1] + self.rooms[k][j-1, 1:-1, 2:] + self.rooms[k][j-1, 1:-1, 0:-2]-4*self.rooms[k][j-1, 1:-1 , 1:-1])
                self.rooms[k][j, -1 , :] = self.rooms[k][j, -2 , :]
                self.rooms[k][j, 0 , :] = self.rooms[k][j, 1 , :]
                self.rooms[k][j, : , -1] = self.rooms[k][j, : , -2]
                self.rooms[k][j, : , 0] = self.rooms[k][j, : , 1] 
                for l in self.radiators[k]: #pętla po grzejnikach w pokoju
                    try:
                        if np.mean(self.rooms[k][j-1, : , :]) <= l[2]:
                            self.matrix[j, l[0] , l[1]] += h_t*f
                    except IndexError:
                        pass
            for m in self.doors:
                self.matrix[j, m[0] , m[1]] = self.matrix[j-1, m[0] , m[1]] + diff_coeff*h_t/h_x**2*(self.matrix[j-1, m[0]+1, m[1]] + self.matrix[j-1, m[0]-1, m[1]] + self.matrix[j-1, m[0], m[1]+1] + self.matrix[j-1, m[0], m[1]-1]-4*self.matrix[j-1, m[0] , m[1]])
            for n in self.windows:
                self.matrix[j, n[0] , n[1]] = 283 #outside temperature
                    
        return self.matrix
        
borders = {
    1 : [(0, 0), (0,15), (10,15), (10,0)], 
    2 : [(10, 0), (10,15), (22,15), (22,0)],
    3 : [(22, 0), (22,15), (30,15), (30,0)],
    4 : [(0, 15), (0,18), (30,18), (30,15)],
    5 : [(0, 18), (0,30), (15,18), (15,30)],
}

radiators = {
    1 : [(5, 1, 296)], #(y, x, max_temperature)
    2 : [(15, 1, 296)],
    3 : [(25, 1, 296)],
    4 : [],
    5 : [(8, 28, 290)],
}

doors = [(5,14),(5,15), (15,14),(15,15), (25,14),(25,15), (9,6),(10,6), (21,6),(22,6), (5,17),(5,18)]
windows = [(5,0), (15,0), (25,0), (29,6), (0,6), (0,25), (8,29)]


a = house((100,100), 1, borders, radiators, doors, windows)

In [3]:
solution_d_cp = a.calculate()[0::60, :, :]
h_t = 1
t = np.arange(0, 60*60+h_t, h_t)
t_cp = t[60::]

x = np.arange(0, np.shape(solution_d_cp)[2], 1)
y = np.arange(0, np.shape(solution_d_cp)[1], 1)



fig = plt.figure(figsize=(5, 5), facecolor='white')
fig.suptitle("My house")

gs = gridspec.GridSpec(1, 1)

ax1 = plt.subplot(gs[0, 0])

ax1.set_xlim((np.min(x), np.max(x)))
ax1.set_ylim((np.max(y), np.min(y)))
ax1.set_xlabel("$x$")
ax1.set_ylabel("$y$")
ax1.set_title("Dirichlet boundary condition")


pcolormesh_d = ax1.pcolormesh(x, y, solution_d_cp[0,:,:], shading='gouraud',vmin=273, vmax=303)

cb1 = fig.colorbar(pcolormesh_d,ax=ax1)

def animation(j):
    pcolormesh_d.set_array(solution_d_cp[j,:, :].ravel())
    ax1.set_title(j)
    return pcolormesh_d

anim = anm.FuncAnimation(fig,
                         func = animation,
                         frames = solution_d_cp.shape[0],
                         interval = 100,
                         blit = False
                         )
plt.close()
plt.rc('animation', html='jshtml')
anim